In [2]:
!pip install transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 23.5 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 31.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 771.9/771.9 kB 31.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 31.2 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 33.8 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.3/78.3 kB 45.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 173.2/173.2 kB 61.2 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip


In [ ]:
# Use a pipeline as a high-level helper
from transformers import pipeline

pipe = pipeline("text-generation", model="beomi/KoAlpaca-Polyglot-5.8B")

# Load model directly
from transformers import AutoTokenizer, AutoModelForCausalLM

tokenizer = AutoTokenizer.from_pretrained("beomi/KoAlpaca-Polyglot-5.8B")
model = AutoModelForCausalLM.from_pretrained("beomi/KoAlpaca-Polyglot-5.8B").to("cuda")

In [1]:
import torch
from transformers import pipeline, AutoModelForCausalLM, AutoTokenizer
import pandas as pd

MODEL = 'beomi/KoAlpaca-Polyglot-12.8B'

# 모델 로딩
model = AutoModelForCausalLM.from_pretrained(
    MODEL,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True,
).to(device="cuda", non_blocking=True)
model.eval()

# 토크나이저 로딩
tokenizer = AutoTokenizer.from_pretrained(MODEL)

# 파이프라인 설정
pipe = pipeline(
    'text-generation', 
    model=model,
    tokenizer=tokenizer,
    device=0
)

def generate_dominant_tone_conversation(prompt):
    context = "갈등 대화"
    query = f"### 질문: {prompt}\n\n### 맥락: {context}\n\n### 답변:"
    response = pipe(
        query, 
        do_sample=True, 
        max_length=512,
        temperature=0.7,
        top_p=0.9,
        return_full_text=False,
        eos_token_id=tokenizer.eos_token_id,
    )
    return response[0]['generated_text'].strip()

# 데이터 불러오기
data_path = "/workspace/train.csv"
data = pd.read_csv(data_path)

# 데이터 증강
augmented_data = []
save_path = "/workspace/dominant_tone_data_transformers.csv"

for index, row in data.iterrows():
    conversation = row['conversation']
    augmented_conversation = generate_dominant_tone_conversation(conversation)

    if augmented_conversation:
        augmented_data.append({'class': row['class'], 'conversation': augmented_conversation})

    # 피드백을 위한 출력 (원본 대화와 생성된 대화를 보여줌)
    print("Original Conversation:")
    print(conversation)
    print("\nAugmented Conversation:")
    print(augmented_conversation)
    print("-" * 50)

    # 대화문이 2개 생성될 때마다 저장
    if (index + 1) % 2 == 0:
        augmented_df = pd.DataFrame(augmented_data)
        augmented_df.to_csv(save_path, mode='a', header=(index == 1), index=False)
        augmented_data = []


Loading checkpoint shards:   0%|          | 0/28 [00:00<?, ?it/s]

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


Original Conversation:
지금 너 스스로를 죽여달라고 애원하는 것인가?
 아닙니다. 죄송합니다.
 죽을 거면 혼자 죽지 우리까지 사건에 휘말리게 해? 진짜 죽여버리고 싶게.
 정말 잘못했습니다.
 너가 선택해. 너가 죽을래 네 가족을 죽여줄까.
 죄송합니다. 정말 잘못했습니다.
 너에게는 선택권이 없어. 선택 못한다면 너와 네 가족까지 모조리 죽여버릴거야.
 선택 못하겠습니다. 한번만 도와주세요.
 그냥 다 죽여버려야겠군. 이의 없지?
 제발 도와주세요.

Augmented Conversation:
너 스스로를 죽여달라는 말은 자살을 시도하는 사람들이 하는 말이지만, 가족과의 갈등에서도 나타날 수 있습니다. 예를 들어, 부모님이나 배우자, 자녀 등과 대화하면서 자신이 무시당하고, 부적절하게 대우받았다고 느낄 때 이에 대한 분노를 표현하는 방법으로 "너 스스로를 죽여봐"라는 말을 사용할 수 있습니다. 이는 상대방을 공격하는 것과 같은 의미로, 상대방의 약점을 찌르거나 모욕하는 말이 될 수 있습니다. 따라서 이러한 말을 사용할 때는 상황에 맞게 사용해야 하며, 상대방의 마음을 고려해야 합니다.
--------------------------------------------------


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


Original Conversation:
길동경찰서입니다.
9시 40분 마트에 폭발물을 설치할거다.
네?
똑바로 들어 한번만 더 얘기한다.
장난전화 걸지 마시죠. 
9시 40분 마트에 폭발물이 터지면 다 죽는거야. 
장난전화는 업무방해죄에 해당됩니다.
판단은 너에게 달려있다. 길동경찰서에도 폭발물 터지면 꽤나 재미있겠지.
선생님 진정하세요.
난 이야기했어. 경고했다는 말이야.

Augmented Conversation:
해당 경찰관은 협박죄로 처벌될 가능성이 높습니다. 하지만, 대화의 내용에 따라 경찰관의 대응에 따라 상황에 따라서는 공무집행방해죄가 추가될 가능성도 있습니다. 

전화를 건 사람이 "한번 더 얘기한다"며 경찰관을 협박한 경우, 해당 경찰관은 협박죄로 처벌될 가능성이 높습니다. 

전화를 건 사람이 "9시 40분에 마트에 폭발물을 설치할 것이다"라는 내용으로 협박한 경우, 이는 협박죄에 해당됩니다. 

만약, 전화를 건 사람이 "9시 40분에 마트에 폭발물이 터지면 다 죽는 거야"라는 내용으로 협박한 경우, 이는 협박죄에 해당되며, 상황에 따라 공무집행방해죄가 추가될 가능성도 있습니다. 

따라서, 전화를 건 사람의 협박의 내용과 그 방법, 경찰관의 대응에 따라 상황이 달라질 수 있으므로, 구체적인 상황을 파악하기 위해서는 전문가의 조언을 받는 것이 좋습니다.
--------------------------------------------------


...

Original Conversation:
내가 지금 너 아들 김길준 데리고 있어. 살리고 싶으면 계좌에 1억만 보내
예.? 선생님 진정하시고 우리 말로 해결합시다.
말로? 지금 상황이 장난같아?
제발 저희 아들만은 건드리지 말아 주십쇼.
그러면 돈 보내.
당장은 돈이 그만큼 없어서. 일단 있는돈 2000만원만 먼저 보내도 되겠습니까??
일단 보내고 목요일까지 나머지 돈 보내
예 알겠습니다.
안그러면 너 아들은 죽는다
제발. 부탁드립니다.

Augmented Conversation:
김길준 군의 아버지가 카카오톡으로 상담한 내용의 대화를 살펴보면, 김길준 군이 납치된 상황에서 돈을 요구하는 납치범과 이를 방지하려는 아버지 사이에 대화가 이루어졌습니다. 

납치범은 아들을 납치하고 있는 상황에서 돈을 요구하며, 만약 돈을 입금하지 않으면 아들을 살해하겠다고 협박합니다. 이에 대해 아버지는 대화를 통해 자신이 가지고 있는 돈이 충분하지 않은 상황에서 일단 2000만원을 입금하였습니다. 

이후 아버지는 카카오톡으로 돈을 입금하였으나, 납치범이 돈을 받지 않으며, 아들을 살해하겠다는 협박을 계속하였습니다. 이에 아버지는 다시 카카오톡으로 "돈을 보냈는데 왜 살려주지 않느냐"며 따지고, 납치범은 "그러면 지금 돈을 또 보내. 이 *같은 새끼야"라고 욕설과 함께 협박을 이어갔습니다. 

이러한 대화 내용을 살펴보면, 김길준 군은 카카오톡으로 아버지와 대화를 하며 납치 상황을 알리고 도움을 구하려고 했습니다. 하지만, 카카오톡 대화만으로는 납치범을 검거하기에는 어려움이 있었습니다. 

결국, 김길준 군은 돈을 입금한 뒤에야 카카오톡에서 납치범과의 대화가 가능했고, 대화를 통해 납치범이 원하는 것은 돈이었음을 알게 되었습니다. 김길준 군의 아버지는 아들을 납치한 범인과 카카오톡 대화를 하며 돈을 입금하는 등, 적극적인 대처를 하였지만, 대화 내용에서는 김길준 군을 걱정하는 마음이 느껴지기도 했습니다.
-----------------------------------------

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


Original Conversation:
나는 씨 같은 사람 보면 참 신기하더라. 어떻게 저렇게 살지.
왜 그래. 들리겠어.
들리라고 해. 아니 일 못해 눈치 없어. 본인도 슬슬 깨달아야 되지 않나?
하긴 그래서 저번에 부장님도.
그렇다니깐! 부장님이 진짜 착하신 분인데 오죽 답답했으면 말을 했겠어?
그러게.
회사생활 같이 한게 몇년인데 대답 하나 제대로 네 하고 싹싹하게 하는걸 못봤어.
나도 그건 못본거 같다.
지금도 그래. 야 야! 너 바로 앞에서 얘기하는데 귀가 먹어서 안들리는거니 안들리는척 하는거니? 뭐 말 좀 해봐?
야 너 왜 그래.
말씀이 너무 심하신거 아니에요?

Augmented Conversation:
"씨 같은 사람 보면 참 신기하더라. 어떻게 저렇게 살지?" 라는 말은 상대방을 비하하거나 조롱하는 뉘앙스가 담긴 표현입니다. 이러한 표현을 사용하는 것은 상황에 따라 법적인 문제가 발생할 수 있습니다. 예를 들어, 상대방의 인격을 훼손하는 것과 같은 발언을 한다면 모욕죄에 해당할 수 있습니다. 따라서, 이러한 표현을 사용하지 않는 것이 좋습니다.

"뭐뭐 같다"라는 표현은 사람들의 말이나 행동이 상식적으로 이해하기 어려운 경우에 자주 사용됩니다. 하지만, 이러한 표현 역시 상황에 따라 모욕죄가 될 수 있습니다. 따라서, 사용하는 경우에는 신중하게 사용해야 합니다. 

"씨"는 종자를 의미하는 말로, 상대방을 비하하거나 조롱하는 상황에서 사용될 경우 모욕죄가 될 수 있습니다. 

따라서, 이러한 표현을 사용하지 않는 것이 좋습니다.
--------------------------------------------------


Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


Original Conversation:
누구맘대로 여기서 장사하래?
이게 무슨일입니까?
남의 구역에서 장사하려면 자릿세를 내야지.
관청에 신고다하고 적법하게 장사하는 건데 자릿세라뇨?
그거랑 상관없이 여기는 우리 구역인데 우리 구역에 장사하려면 자릿세를 내라고.
못 드립니다.
우리 구역이니까 우리가 마음대로 할거라고. 좋은말로 할 때 자릿세를 내.
못 드립니다.
아 그럼 여기 업장 깽판쳐도 된다 이거지?
아. 아닙니다. 드. 드리겠습니다.

Augmented Conversation:
개인과 국가 간의 분쟁에서는 주로 힘의 논리가 적용됩니다. 개인이 국가를 상대로 승리하기는 어렵기 때문에, 대부분의 경우 국가의 요구에 따라 협의점을 찾거나 일부 손해를 감수하고 영업을 지속하는 경우가 많습니다. 

하지만, 내부적인 문제로 인해 발생하는 분쟁에서는 상황에 따라 다른 해결책이 존재합니다. 예를 들어, 가게에서 옆 가게에 피해를 주는 경우나 주차 문제 등에서는 적절한 협의가 필요할 수 있습니다. 

어떤 상황에서도 법적인 문제가 발생할 가능성이 있으므로, 가능한 경우에는 대화로 해결하는 것이 좋습니다. 그러나, 강제력을 동원해야만 하는 경우도 발생하기 때문에 상황에 따라 경찰을 부르는 것도 고려해야 합니다.
--------------------------------------------------
Original Conversation:
희정씨
네?
주말에 시간이 넘쳐나나봐
갑자기 왜그러세요?
손이 빤짝빤짝 네일했니?
네 여름이라 기분전환으로.
어휴 그손으로 결제 받으러 가면 윗분들 눈 아프시겠다 정신사나워
그냥 파스텔톤으로만 칠한건데.
희정씨가 윗사람이야?? 얼른 가서 지우고와
.네

Augmented Conversation:
해당 상황은 누군가가 희정씨의 행동에 대해 언급한 것이며, 이에 대한 희정씨의 반응이 궁금합니다. "손이 빤짝빤짝 네일했니?"라는 문장은 긍정적인 뉘앙스를 지니고 있지 않으며, 희정씨의 네일아트에 대한 부정적인 시각을 드러내고 있습니다. 이

In [6]:
!pip install accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.2/251.2 kB 9.0 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip
